In [1]:
import torch
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "2"

import sys
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))

#use gpu number 3 
device=torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Using device:", device)

#file_id=6448
file_id=23114

base_path="/home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/"
file_dry=os.path.join(base_path, "dry",str(file_id),"vocals.wav")
file_wet=os.path.join(base_path, "wet",str(file_id),"vocals.wav")

import soundfile as sf

print("Loading files:", file_dry, file_wet)
dry, sr = sf.read(file_dry)
print("Loading files:", file_dry, file_wet)
wet, sr = sf.read(file_wet)
print("files loaded")

#file_dry_fxnorm, sr=sf.read(file_dry_fxnorm_dr)
#file_wet_fxnorm, sr=sf.read(file_wet_fxnorm_dr)

dry=torch.from_numpy(dry.T).float().unsqueeze(0)
wet=torch.from_numpy(wet.T).float().unsqueeze(0)

#dry_fxnorm=torch.from_numpy(file_dry_fxnorm.T).float().unsqueeze(0)

dry=dry.mean(dim=1, keepdim=True)

#dry_fxnorm=torch.from_numpy(file_dry_fxnorm.T).float().unsqueeze(0)


start_t=15*sr
segment_length = 524288
wet_segment = wet[...,start_t:start_t + segment_length]


import pyloudnorm as pyln
meter = pyln.Meter(sr)
normaliser = lambda x: pyln.normalize.loudness(
    x, meter.integrated_loudness(x), -18.0
)

print("dry", dry.shape, dry.min(), dry.max())

dry = torch.from_numpy(normaliser(dry.numpy().T).T).float().to(device)
#wet = torch.from_numpy(normaliser(wet.numpy().T).T).float().to(device)
#dry_fxnorm = torch.from_numpy(normaliser(dry_fxnorm.numpy().T).T).float().to(device)


print("dry", dry.shape,dry.min(), dry.max())
dry_segment = dry[...,start_t:start_t + segment_length]


from IPython.display import Audio

#Audio(dry_segment[0].cpu().numpy(), rate=sr, normalize=False)
Audio(wet_segment[0].cpu().numpy(), rate=sr, normalize=True)

Using device: cuda
Loading files: /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/dry/23114/vocals.wav /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/wet/23114/vocals.wav
Loading files: /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/dry/23114/vocals.wav /home/eloi/projects/project_mfm_eloi/audio_examples/TM_val/wet/23114/vocals.wav
files loaded
dry torch.Size([1, 1, 7014686]) tensor(-0.7464) tensor(0.7499)
dry torch.Size([1, 1, 7014686]) tensor(-0.8735, device='cuda:0') tensor(0.8776, device='cuda:0')


In [24]:
#load generator model
import hydra
import torch
import os
import sys
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))
from hydra import initialize, initialize_config_module, initialize_config_dir, compose
import utils.training_utils as tr_utils

config_file_rel="../conf"
config_path="/home/eloi/projects/project_mfm_eloi/src/conf"
config_name="conf_MDW2_mapper_blackbox_predictive_fxenc2048AFv3CLAP_paired.yaml"
model_dir = "/data5/eloi/experiments/MDW2_mapper_blackbox_predictive_fxenc2048AFv3CLAP_paired"
ckpt="mapper_blackbox_TCN-25000.pt"

overrides = [
    f"model_dir={model_dir}",
    f"tester.checkpoint={ckpt}",
    "tester.cfg_scale=1.0",
]


with initialize(version_base=None, config_path=config_file_rel):
    args = compose(config_name=config_name, overrides=overrides)


if not os.path.exists(args.model_dir):
        raise Exception(f"Model directory {args.model_dir} does not exist")


device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

print("loading diff_params")
diff_params=hydra.utils.instantiate(args.diff_params)

print("loading network")
network=hydra.utils.instantiate(args.network)
network=network.to(device)
state_dict = torch.load(os.path.join(args.model_dir,args.tester.checkpoint), map_location=device, weights_only=False)

tr_utils.load_state_dict(state_dict, network=network)


#sampler = hydra.utils.instantiate(args.tester.sampler, network, diff_params, args, )
#
#def generate_samples(x, input_type="dry"):
#    B, N, C, L = x.shape  # B is the batch size, N is the number of tracks, C is the number of channels and L is the length of the audio
#    shape=sampler.diff_params.default_shape
#    shape= [B, *shape[1:]]  # B is the batch size, we want to sample B samples
#    with torch.no_grad():
#        is_wet= "wet" in input_type
#        cond, x_preprocessed=sampler.diff_params.transform_forward(cond,  is_condition=True, is_test=True, clusters=cluster, taxonomy=taxonomy, masks=masks, is_wet=is_wet)
#        preds, noise_init = sampler.predict_conditional(shape, cond=cond, cfg_scale=args.tester.cfg_scale, device=device, taxonomy=taxonomy, masks=masks)
#    
#    return preds
        



/home/eloi/myenv/lib/python3.11/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'conf_MDW2_mapper_blackbox_predictive_fxenc2048AFv3CLAP_paired.yaml': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)


loading diff_params


/home/eloi/myenv/lib/python3.11/site-packages/torchaudio/functional/functional.py:584: UserWarning: At least one mel filterbank has all zero values. The value for `n_mels` (128) may be set too high. Or, the value for `n_freqs` (513) may be set too low.
  warnings.warn(
/home/eloi/myenv/lib/python3.11/site-packages/torchaudio/functional/functional.py:584: UserWarning: At least one mel filterbank has all zero values. The value for `n_mels` (128) may be set too high. Or, the value for `n_freqs` (257) may be set too low.
  warnings.warn(
/home/eloi/myenv/lib/python3.11/site-packages/torch/nn/_reduction.py:51: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


loading network


Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Load the specified checkpoint /data5/eloi/checkpoints/laion_clap/music_audioset_epoch_15_esc_90.14.patched.pt from users.
Loading state dict
dict_keys(['it', 'network', 'optimizer', 'ema', 'args'])
Attempt 1: trying with strict=True


True

In [25]:

import math
import omegaconf
Fxencoder_kwargs={
    "distance_type": "cosine",
    "ckpt_path": "/home/eloi/projects/project_mfm_eloi/src/utils/feature_extractors/ckpt/fxenc_plusplus_default.pt"
}
Fxencoder_kwargs= omegaconf.OmegaConf.create(Fxencoder_kwargs)

from evaluation.feature_extractors import load_fx_encoder_plusplus_2048
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
feat_extractor = load_fx_encoder_plusplus_2048(Fxencoder_kwargs, device)

from utils.AF_features_embedding_v2 import AF_fourier_embedding

AFembedding= AF_fourier_embedding(device=device)

def fxencode_fn(x):
    """
    x: tensor of shape [B, C, L] where B is the batch size, C is the number of channels and L is the length of the audio
    """
    z=feat_extractor(x)
    z= torch.nn.functional.normalize(z, dim=-1, p=2)  # normalize to unit variance
    z= z* math.sqrt(z.shape[-1])  # rescale to keep the same scale

    z_af,_=AFembedding.encode(x)
    #embedding is l2 normalized, normalize to unit variance
    z_af=z_af* math.sqrt(z_af.shape[-1])  # rescale to keep the same scale

    #concatenate z and z_af (rescaling with sqrt(dim) to keep the same scale)

    z_all= torch.cat([z, z_af], dim=-1)

    #now L2 normalize
    norm_z= z_all/ math.sqrt(z_all.shape[-1])  # normalize by dividing by sqrt(dim) to keep the same scale

    return norm_z

FXenc=fxencode_fn

OutOfMemoryError: CUDA out of memory. Tried to allocate 20.00 MiB. GPU 0 has a total capacity of 79.15 GiB of which 20.62 MiB is free. Process 3599472 has 63.96 GiB memory in use. Including non-PyTorch memory, this process has 15.14 GiB memory in use. Of the allocated memory 14.54 GiB is allocated by PyTorch, and 108.13 MiB is reserved by PyTorch but unallocated. If reserved but unallocated memory is large try setting PYTORCH_CUDA_ALLOC_CONF=expandable_segments:True to avoid fragmentation.  See documentation for Memory Management  (https://pytorch.org/docs/stable/notes/cuda.html#environment-variables)

In [22]:
from utils.data_utils import apply_RMS_normalization
device=torch.device("cuda" if torch.cuda.is_available() else "cpu")
x=dry_segment.to(device)

y=wet_segment.to(device)

x=apply_RMS_normalization(x, -25, device=device)

z=FXenc(y)

y=apply_RMS_normalization(y, -25, device=device)
print("z shape:", z.shape)

diff_params.save_embedding(network,x, z)

shape=diff_params.default_shape
t=0.1
t=torch.tensor(t, device=device).unsqueeze(0)
#n=diff_params.sample_prior(shape, t=t)
#print("n shape:", n.shape, n.std())

input, target, cnoise, cskip, cout, cin = diff_params.prepare_train_preconditioning(y, t)

#x0=diff_params.denoiser(xT, network, t, cond=x)
estimate = network(input, diff_params.embedding, time_cond=cnoise.unsqueeze(-1), input_concat_cond=x)

if target.ndim==2 and estimate.ndim==3:
    estimate=estimate.squeeze(1)

error = estimate - target

x_hat= cskip * (input/cin) + cout * estimate

print("x_hat shape:", x_hat.shape, "x shape:", x.shape, "y shape:", y.shape)



z shape: torch.Size([1, 2112])
x_hat shape: torch.Size([1, 2, 524288]) x shape: torch.Size([1, 1, 524288]) y shape: torch.Size([1, 2, 524288])


In [23]:
error_dict=diff_params.MSS_loss_fn(x_hat, y)

loss_dict= {
    "l2": (error**2).mean(-1).mean(-1).unsqueeze(-1),
    "MSS_loss_ms": error_dict["loss_mss_midside"].mean(-1)* diff_params.loss_weights["loss_mss_midside"],
    "MSS_loss_lr": error_dict["loss_mss_lr"].mean(-1)* diff_params.loss_weights["loss_mss_lr"],
}
print("loss_dict:", loss_dict)

loss_dict: {'l2': tensor([[0.2581]], device='cuda:0', grad_fn=<UnsqueezeBackward0>), 'MSS_loss_ms': tensor([0.3580], device='cuda:0', grad_fn=<MulBackward0>), 'MSS_loss_lr': tensor([0.3099], device='cuda:0', grad_fn=<MulBackward0>)}


In [14]:
import IPython.display as ipd
ipd.display(ipd.Audio(x0[0].detach().cpu().numpy(), rate=sr, normalize=True))